In [3]:
import geopandas as gpd    
import os
import pandas as pd
from glob import glob
import tempfile
import shutil

In [2]:
import pystac_client
import planetary_computer

In [5]:
def combine_slosh_extents(slosh_extent_dir):
    #read in and combine slosh extent
    combined_extent = []
    for file_name in os.listdir(slosh_extent_dir):
        os.path.join(file_name, slosh_extent_dir)
    slosh_extent_file_paths = glob(slosh_extent_dir + "/*.shp")
    slosh_extent_gdf = pd.concat([gpd.read_file(p) for p in slosh_extent_file_paths], 
                                 ignore_index=True)
    return slosh_extent_gdf


In [5]:
def unzip_read_shp(file_path, output_dir):
    os.makedirs(output_dir, exist_ok=True)
    shutil.unpack_archive(file_path, output_dir)
    data_path = glob(output_dir + "/*.shp")[0]
    return gpd.read_file(data_path)

In [12]:
shutil.unpack_archive("/hpc/home/csr33/cb_2019_us_tract_500k.zip",
                      "/hpc/group/borsuklab/political-boundaries")
#gpd.read_file("/hpc/group/borsuklab/political-boundaries/cb_2019_us_tract_500k.zip")

ReadError: /hpc/home/csr33/cb_2019_us_tract_500k.zip is not a zip file

In [10]:
gpd.read_file("/hpc/home/csr33/cb_2019_us_tract_500k.zip")

DriverError: '/vsizip//hpc/home/csr33/cb_2019_us_tract_500k.zip' does not exist in the file system, and is not recognized as a supported dataset name.

In [8]:
slosh_extent_dir = "/hpc/group/borsuklab/nat_hazard_data/slosh/unzip/v3_extent_shp"
slosh_extent_gdf = combine_slosh_extents(slosh_extent_dir)

In [10]:
country_boundary=gpd.read_file("/hpc/group/borsuklab/political-boundaries/states/generalized-conus-country-boundary.shp")

In [23]:
slosh_extent_in_usa = gpd.clip(slosh_extent_gdf, country_boundary.to_crs(slosh_extent_gdf.crs))

In [25]:
geojson_dict

{'type': 'MultiPolygon',
 'coordinates': [(((-68.813168000203, 46.3957130001549),
    (-68.81309300034167, 46.3957130001549),
    (-68.81301100015747, 46.395712000108745),
    (-68.81289700029629, 46.395712000108745),
    (-68.81207800029944, 46.3957079999243),
    (-68.81188200025406, 46.3957069998782),
    (-68.81107900009573, 46.3957019996476),
    (-68.81093899993488, 46.3957019996476),
    (-68.81082400002754, 46.3957019996476),
    (-68.81056699986709, 46.395699999555404),
    (-68.81029700000653, 46.39569800036247),
    (-68.81011699979967, 46.395697000316375),
    (-68.81004400003053, 46.395697000316375),
    (-68.80994499996171, 46.395697000316375),
    (-68.8098970004462, 46.39569600027028),
    (-68.80903999959628, 46.39569200008577),
    (-68.80888999987354, 46.395691000039676),
    (-68.80801399994613, 46.39568699985523),
    (-68.80789599990044, 46.395685999809075),
    (-68.80699100043427, 46.39568099957853),
    (-68.80691899981196, 46.39568099957853),
    (-68.80596299

In [76]:
from shapely.geometry import Polygon

point1 = (-75.754727, 39.059650)
point2 = (-75.003601, 38.453883)
 

# The points are the bottom left and top right corners of the rectangle
polygon = [point1, (point2[0], point1[1]), point2, (point1[0], point2[1]), point1]


[[-75.754727, 39.05965],
 [-75.003601, 39.05965],
 [-75.003601, 38.453883],
 [-75.754727, 38.453883],
 [-75.754727, 39.05965]]

In [82]:
# Assuming 'gdf' is your GeoDataFrame and 'geometry' is your column with the Polygon
#polygon = slosh_extent_in_usa['geometry'].iloc[1]

# Get the GeoJSON dictionary representation
#geojson_dict = polygon.__geo_interface__

# Convert to your area_of_interest format
area_of_interest = {
    "type": "Polygon", #geojson_dict["type"],
    "coordinates": [[list(tup) for tup in polygon]] #geojson_dict["coordinates"][0]#[0]  # We only need the outer ring
}

In [83]:
area_of_interest

{'type': 'Polygon',
 'coordinates': [[[-75.754727, 39.05965],
   [-75.003601, 39.05965],
   [-75.003601, 38.453883],
   [-75.754727, 38.453883],
   [-75.754727, 39.05965]]]}

In [70]:
catalog = pystac_client.Client.open(
    "https://planetarycomputer.microsoft.com/api/stac/v1",
    modifier=planetary_computer.sign_inplace,
)

In [87]:
range_new = "2020-01-01/2024-01-31"
search_new = catalog.search(
    collections=["naip"], intersects=area_of_interest, datetime=range_new
)

In [89]:
items_new = search_new.item_collection()

In [90]:
items_new

In [ ]:

#Install using Christoph Golke Wheel; https://www.lfd.uci.edu/~gohlke/pythonlibs/#shapely
import shapely
import rasterio
from geopy.geocoders import Nominatim
from rasterio.windows import Window 
#Import module with functions
import src.az_proc as ap
import argparse

In [ ]:
x = gpd.read_file("/work/csr33/quads/map_indexes_QD12K/map_indexes\quads12k_a_extract.shp")

In [ ]:
def get_args_parse():
    parser = argparse.ArgumentParser(
        description='obtain tile name and tile url')
    parser.add_argument('--blob_root', type=str, default='https://naipeuwest.blob.core.windows.net/naip',
                        help='Define Microsoft Azure Blob Root; The(preferred) copy of NAIP in the West Europe Azure region')
    parser.add_argument('--lat_lon_dir', type=str, help='Directory holding datasets of lat lons')
    parser.add_argument('--quad_dir', type=str, help='Directory holding dataset of quads')
    parser.add_argument('--output_dir', type=str, default=None,
                        help='Directory to save outputs')
    parser.add_argument('--tile_names_tile_urls_filename', type=str, default=None,
                        help='Filename to save tile names and urls')


    args = parser.parse_args()
    return args

In [ ]:
slosh_extent_gdf

In [ ]:

def collected_quads_to_tile_name_tile_url(quads, blob_root): 
    """
    #Tiles are stored at: [blob root]/v002/[state]/[year]/[state]_[resolution]_[year]/[quadrangle]/filename
    #Read in a excel sheet which includes the quadrangle 
    """

    tile_names = []
    tile_urls = []
    file_name_index = {'m': 0, 'qqname': 1, 'direction': 2, 'YY': 3, 'resolution': 4, 'capture_date': 5,
                       'version_date': 5}
    two_digit_state_resolution = ["al", "ak", "az", "ar", "ca", "co", "ct", "de", "fl", "ga",
                                  "hi", "id", "il", "in", "ia", "ks", "ky", "la", "me", "md",
                                  "ma", "mi", "mn", "ms", "mo", "mt", "ne", "nv", "nh", "nj",
                                  "nm", "ny", "nc", "nd", "oh", "ok", "or", "pa", "ri", "sc",
                                  "sd", "tn", "tx", "ut", "vt", "va", "wa", "wv", "wi", "wy"]

    for index, row in quads.iterrows():
        file_name = row[0].split('_')  # filename
        state = row[1].lower()  # state
        year = row[2]  # YYYY

        if state in two_digit_state_resolution:
            resolution = file_name[file_name_index["resolution"]][1:3] + "cm"
        else:
            resolution = file_name[file_name_index["resolution"]] + "cm"
        quadrangle = file_name[file_name_index["qqname"]][0:5]  # qqname

        tile_name = file_name + '.tif'
        tile_names.append(tile_name)
        tile_urls.append(os.path.join(blob_root, "v002", state, str(year), 
                                      state + '_' + str(resolution) + '_' + str(year),
                                      str(quadrangle), tile_name))
    return (tile_names, tile_urls)

In [ ]:
def get_urls_from_quads(quad_dir): 
    tile_names_tile_urls = pd.DataFrame() #dataframe to hold all tile_names and urls
    quad_paths = glob(quad_dir + "/*.csv")
    for quad_path in quad_paths:
        quad_dataset = pd.read_csv(quad_path) #read in sheet of quadrangles
        tile_names, tile_urls = collected_quads_to_tile_name_tile_url(quad_dataset, blob_root) # identify filespaths/urls for quads of interest
        quad_names_urls = pd.DataFrame({"tile_name": tile_names, "tile_url": tile_urls})
        tile_names_tile_urls = pd.concat([tile_names_tile_urls, quad_names_urls])
    return tile_names_tile_urls

In [ ]:
def tile_name_tile_url_characteristics(tile_names_tile_urls, output_path = None): 
    """tabulates the tile characteristics (the states, year resolution ranges), 
      returns the tile charcateristics 
       (quadrange names, the filenames,the states, year resolution ranges)

    Args:
        file_loc (str): The file location of the spreadsheet
        print_cols (bool): A flag used to print the columns to the console
            (default is False)

    Returns:
        list: a list of strings representing the header columns
    """

    state_array = np.empty((len(tile_names_tile_urls), 1), dtype=object)
    year_array = np.empty((len(tile_names_tile_urls), 1))
    quad_array = np.empty((len(tile_names_tile_urls), 1))
    resolution_array = np.empty((len(tile_names_tile_urls), 1), dtype=object)
    filename_array = np.empty((len(tile_names_tile_urls), 1), dtype=object)

    for i in range(len(tile_names_tile_urls)):
        state_array[i] = tile_names_tile_urls[i, 1].split('/')[5]
        year_array[i] = tile_names_tile_urls[i, 1].split('/')[6]
        quad_array[i] = tile_names_tile_urls[i, 1].split('/')[8]
        filename_array[i] = tile_names_tile_urls[i, 1].split('/')[9]
        resolution_array[i] = tile_names_tile_urls[i, 1].split('/')[-3].split('_')[1]

    state_abbreviations = np.unique(state_array)
    num_states = len(state_abbreviations)
    years = np.unique(year_array)
    resolutions = np.unique(resolution_array)

    print("the number of tiles includes", len(tile_names_tile_urls))
    print("The number of states included", num_states)
    print("Postal abriviations of the states included", state_abbreviations)
    print("The years in which the images were collected", years)
    print("The resolutions of the images", resolutions)
    if output_path is not None:
        np.save(os.path.join(output_path, 'states_in_tile_urls.npy'), state_abbreviations)

    return num_states, state_abbreviations, years, resolutions, quad_array, filename_array

In [ ]:

class DownloadProgressBar():
    """
    A progressbar to show the completed percentage and download speed for each image downloaded using urlretrieve.

    https://stackoverflow.com/questions/37748105/how-to-use-progressbar-module-with-urlretrieve
    """

    def __init__(self):
        self.pbar = None

    def __call__(self, block_num, block_size, total_size):
        if not self.pbar:
            self.pbar = progressbar.ProgressBar(max_value=total_size)
            self.pbar.start()

        downloaded = block_num * block_size
        if downloaded < total_size:
            self.pbar.update(downloaded)
        else:
            self.pbar.finish()


class NAIPTileIndex:
    """
    Utility class for performing NAIP tile lookups by location.
    """

    tile_rtree = None
    tile_index = None
    base_path = None

    def __init__(self, base_path=None):
        blob_root = 'https://naipeuwest.blob.core.windows.net/naip'
        index_files = ["tile_index.dat", "tile_index.idx", "tiles.p"]
        index_blob_root = re.sub('/naip$', '/naip-index/rtree/', blob_root)

        if base_path is None:

            base_path = os.path.join(tempfile.gettempdir(), 'naip')
            os.makedirs(base_path, exist_ok=True)

            for file_path in index_files:
                download_url(index_blob_root + file_path, destination_folder=base_path,
                             destination_filename=base_path + '/' + file_path,
                             progress_updater=DownloadProgressBar())

        self.base_path = base_path
        self.tile_rtree = rtree.index.Index(base_path + "/tile_index")
        self.tile_index = pickle.load(open(base_path + "/tiles.p", "rb"))

    def lookup_tile(self, lat, lon):
        """"
        Given a lat/lon coordinate pair, return the list of NAIP tiles that contain
        that location.

        Returns a list of COG file paths.
        """

        point = shapely.geometry.Point(float(lon), float(lat))
        intersected_indices = list(self.tile_rtree.intersection(point.bounds))

        intersected_files = []
        tile_intersection = False

        for idx in intersected_indices:

            intersected_file = self.tile_index[idx][0]
            intersected_geom = self.tile_index[idx][1]
            if intersected_geom.contains(point):
                tile_intersection = True
                intersected_files.append(intersected_file)

        if not tile_intersection and len(intersected_indices) > 0:
            print('''Error: there are overlaps with tile index, 
                      but no tile completely contains selection''')
            return None
        elif len(intersected_files) <= 0:
            print("No tile intersections")
            return None
        else:
            return intersected_files


def download_url(url, destination_folder, destination_filename=None, progress_updater=None, force_download=False): 
    """
    Download a URL to a a file
    Args:
    url(str): url to download
    destination_folder(str): directory to download folder
    destination_filename(str): the name for each of files to download
    return:
    destination_filename
    """

    # This is not intended to guarantee uniqueness, we just know it happens to guarantee
    # uniqueness for this application.
    if destination_filename is not None:
        destination_filename = os.path.join(destination_folder, destination_filename)
    if destination_filename is None:
        url_as_filename = url.replace('://', '_').replace('/', '_')
        destination_filename = os.path.join(destination_folder, url_as_filename)
    if os.path.isfile(destination_filename):
        print('Bypassing download of already-downloaded file {}'.format(os.path.basename(url)))
        return destination_filename
    #  print('Downloading file {} to {}'.format(os.path.basename(url),destination_filename),end='')
    urllib.request.urlretrieve(url, destination_filename, progress_updater)
    assert (os.path.isfile(destination_filename))
    nBytes = os.path.getsize(destination_filename)
    print('...done, {} bytes.'.format(nBytes))

    return destination_filename

In [ ]:


def main(args):    
    ## Define Microsoft Azure Blob Root
    # The(preferred) copy of NAIP in the West Europe Azure region
    warnings.filterwarnings("ignore")

    ## Load the spatial index of NAIP tiles
    # Spatial index that maps lat/lon to NAIP tiles; we'll load this when we first 
    # need to access it.
    index = None
    if index is None:
        index = ap.NAIPTileIndex()
        
    tile_names_tile_urls_from_lat_lons = ap.get_urls_from_lat_lons(args.lat_lon_dir, index, args.blob_root)
    tile_names_tile_urls_from_quads = ap.get_urls_from_quads(args.quad_dir)
    tile_names_tile_urls = pd.concat([tile_names_tile_urls_from_lat_lons, tile_names_tile_urls_from_quads])
    tile_names_tile_urls = tile_names_tile_urls.drop_duplicates() #remove duplicates
    np.save(os.path.join(args.output_dir, args.tile_names_tile_urls_filename), tile_names_tile_urls) #save
    
    num_states, state_abbreviations, years, resolutions, quad_array, filename_array = ap.tile_name_tile_url_characteristics(tile_names_tile_urls, args.output_dir) #get attributes
    
if __name__ == '__main__':
    ### Get the arguments 
    args = get_args_parse()
    main(args)